In [14]:
import networkx as nx
import matplotlib.pyplot as plt
from sys import getsizeof
import time
import folium
from heapq import heappush, heappop
from fibonacci_heap import Fibonacci_heap

Data import

In [2]:
with open('../data/USA-road-d.CAL.co','r',newline = '\n') as file:
    nodes = file.readlines()
with open('../data/USA-road-d.CAL.gr','r',newline = '\n') as file:
    dis_m = file.readlines()
with open('../data/USA-road-t.CAL.gr','r',newline = '\n') as file:
    dis_t = file.readlines()
    #head = [next(file).splitlines() for x in range(1000)]

Data cleaning

In [3]:
# the first 6 lines are descriptions of the data
nodes = nodes[7:]
dis_m = dis_m[7:]
dis_t = dis_t[7:]

From the nodes file, we keep only the latitude and longitude of each node.

In [4]:
for i in range(len(nodes)):
    nodes[i] = nodes[i][:-1]
    nodes[i] = list(nodes[i].split())[2:]
nodes[0]

['-114315309', '34133550']

Latitude and longitude of each node are strings without float point (e.g ''-114318765''). Since we know that longitude and latitude of California and Nevada go from 32.5-42.0	and 114.0 - 125.0 respectively,  we want to convert that string into a float number in the format : -114.318765. 

In [5]:
for i in range(len(nodes)):
    # just add the comma after the third or second digit
    nodes[i][0] = float(nodes[i][0][0:4]+'.'+nodes[i][0][4:])
    nodes[i][1] = float(nodes[i][1][0:2]+'.'+nodes[i][1][2:])
# at the end we get
nodes[0]

[-114.315309, 34.13355]

Clean data in the same way but for edges

In [6]:
# every row is in the format, 'starting node' \t 'ending node' \t ' distance'
for i in range(len(dis_m)):
    dis_m[i] = dis_m[i][1:]
    dis_t[i] = dis_t[i][1:]
    dis_m[i] = dis_m[i][:-1]
    dis_t[i] = dis_t[i][:-1]    
    dis_m[i] = dis_m[i].split()
    dis_t[i] = dis_t[i].split()

In [7]:
g = nx.DiGraph()
# add nodes
for i in range(len(nodes)):
    # add latitude and longitude as an attribute to each node, in the format of a tuple
    g.add_node(i+1, pos = (nodes[i][0], nodes[i][1]) )
# add edges with spatial distance only, if you want with time distance then just change to dis_t
for i in range(len(dis_m)):
    # not every row of dis_m has numbers as entries, there can also be missing values or just
    # wrong values. For this reason we use 'try'
    try:
        if (int(dis_m[i][0]) in g.nodes() and int(dis_m[i][1]) in g.nodes()): 
            # add as attribute to every edge the distance
            g.add_edge(int(dis_m[i][0]), int(dis_m[i][1]), distance = float(dis_m[i][2]),
                                                                        time = float(dis_t[i][2]))
    except Exception as e:
        print(i, e)
        continue

In [9]:
nx.write_gpickle(g, "../data/complete_graph_di.gpickle.gz")

In [15]:
G = nx.read_gpickle("../data/complete_graph_di.gpickle.gz")

In [16]:
def get_weight(graph, node, next_node, mode):
    if mode == 'n':
        return 1
    elif mode == 't':
        return graph.get_edge_data(node, next_node)['time']
    elif mode == 'm':
        return graph.get_edge_data(node, next_node)['distance']

In [17]:
def dijkstra(graph, start, dest, mode):
    # shortest paths is a dict of nodes
    # whose value is a tuple of (previous node, weight)
    # initialize it with the initial node and set it with wight 0
    shortest_paths = {start: (None, 0)}
    current_node = start
    visited = set()
    
    # create a heap and store the nodes
    # ordered by currend wight
    # heap = []
    heap = Fibonacci_heap()
    
    while current_node != dest:
        # Add current node to the set of visited nodes
        visited.add(current_node)
        # adjacency list, take all edges from the current node
        destinations = [elem[1] for elem in graph.edges(current_node)]
        # take the total weight
        weight_to_current_node = shortest_paths[current_node][1]

        # visit all nodes connected to the current node
        for next_node in destinations:
            # calculate the weight of the current edge
            # weight of the edge + weight of edges previously visited in the path
            weight = get_weight(graph, current_node, next_node, mode) + weight_to_current_node
            
            # add nodes to the heap
            if next_node not in visited and next_node not in heap.nodes:
                #heappush(heap, (weight, next_node))
                heap.enqueue(next_node, weight)
            
            # add new node in shortest path
            # or update it if current path is shorter of previous path
            if next_node not in shortest_paths:
                shortest_paths[next_node] = (current_node, weight)
            else:
                current_shortest_weight = shortest_paths[next_node][1]
                if current_shortest_weight > weight:
                    shortest_paths[next_node] = (current_node, weight)
        
        # if heap is empty we cannot continue
        # and we cannot reach the destination
        #if len(heap) == 0:
         #   return "Not Possible"
        
        if not heap.__bool__():
            return "Not Possible"
        
        # update current_node
        # next node is the destination with the lowest weight
        #current_node = heappop(heap)[1]
        current_node = heap.dequeue_min().m_elem
    
    # Work back through destinations in shortest path
    # create path and reverse it
    path = []
    while current_node is not None:
        path.append(current_node)
        # take previous node from the dict
        next_node = shortest_paths[current_node][0]
        current_node = next_node
    # Reverse path
    path = path[::-1]
    return (path, shortest_paths[path[-1]][1])

In [161]:
t6 = time.time()
d = dijkstra(G, 1, 125478, 't')
print(time.time() - t6)

54.18961763381958


In [18]:
def shortest_ordered_route(graph, start, route, mode):
    if len(route) < 1:
        print("Insert at least 1 node")
        return
    total = 0
    path = [start]
    for elem in route:
        tmp = dijkstra(G, start, elem, mode)
        total += tmp[1]
        path.extend(tmp[0][1:])
        start = elem
    return (path, route, total)

# Task 4

In [19]:
import math
import numpy as np

In [22]:
t = time.time()
print(math.sqrt(23.33333**2 + 144.4444**2))
print(((2)*(100*100))/60)

146.3168786580991
0.07776419321695964


In [78]:
def adj_matrix(graph, l):
    adj_mat = np.zeros((len(l), len(l)))
    i = 0
    for elem in l:
        for j in range(len(l)):
            x1 = G.node[elem]['pos'][::-1][0]
            y1 = G.node[elem]['pos'][::-1][1]
            x2 = G.node[l[j]]['pos'][::-1][0]
            y2 = G.node[l[j]]['pos'][::-1][1]
            if j == len(l) - 1:
                adj_mat[i][j] = 9999999999999999
            else:
                adj_mat[i][j] = math.sqrt((x1-x2)**2 + (y1-y2)**2)
        i = i + 1
    return adj_mat

In [79]:
t3 = time.time()
l = adj_matrix(G, [1, 247, 2522, 12, 24, 125478, 56])
print(time.time()-t3)

0.0005350112915039062


In [75]:
np.where(l[2] == min(l[2]))[0][0]

0

In [79]:
def app_short(graph, l_nodes):
    
    adj_mat = adj_matrix(graph, l_nodes)
    
    path = [0]
    
    current_node = 0
    path = [l_nodes[current_node]]
    
    for _ in range(len(l_nodes) - 1):
        
        adj_mat[:, current_node] = float('inf')
        
        next_node = np.where(adj_mat[current_node] == min(adj_mat[current_node]))[0][0]
        
        current_node = next_node
        path.append(l_nodes[current_node])
        
    return path

In [40]:
shortest_route = app_short(G, [1, 56, 21, 1803, 25, 125478])
shortest_route

[1, 1803, 25, 21, 56, 125478]

In [62]:
t1 = time.time()
test = shortest_ordered_route(G, shortest_route[0], shortest_route[1:], 'n')
print(time.time() - t1)

49.56221842765808


In [64]:
test[2]

978

In [61]:
viz_map(shortest_route, test[0])

In [80]:
shortest_route1 = app_short(G, [1, 5, 8, 25, 896, 47851, 569874, 1122003, 587, 78965, 456987, 125])

In [81]:
shortest_route1

[1, 5, 8, 25, 587, 896, 569874, 456987, 47851, 78965, 1122003, 125]

In [85]:
t1 = time.time()
test1 = shortest_ordered_route(G, shortest_route1[0], shortest_route1[1:], 'n')
print(time.time() - t1)

268.8707649707794


In [89]:
viz_map(shortest_route1, test1[0])

In [87]:
test1[2]

4914

In [31]:
t1 = time.time()
shortest_ordered_route(G, 1, [5, 8, 26, 89, 745, 78965], 'n')
print(time.time() - t1)

67.1891222000122


In [7]:
test = np.zeros((5,5))
test

array([[0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.]])

In [11]:
test[:, 2] = float('inf')

In [12]:
test

array([[ 0.,  0., inf,  0.,  0.],
       [ 0.,  0., inf,  0.,  0.],
       [ 0.,  0., inf,  0.,  0.],
       [ 0.,  0., inf,  0.,  0.],
       [ 0.,  0., inf,  0.,  0.]])

# Visualization

In [15]:
t = time.time()
print(dijkstra(G, 1, 1805456, 't'))
print(time.time() - t)

([1, 1048577, 1766, 1048579, 3, 1049931, 1833, 1678, 1677, 1050044, 1623, 1049878, 1049877, 1621, 1598, 1581, 1580, 1049844, 1050034, 1821, 1504363, 567462, 1504364, 567444, 1504348, 1504349, 567440, 1504345, 1504356, 567454, 1504355, 567453, 1504368, 1504367, 567469, 567475, 567461, 567449, 567450, 567451, 567452, 1504353, 567203, 1504140, 567185, 1504141, 567186, 1504142, 567199, 1504152, 567189, 1504145, 567190, 567194, 1504147, 1504150, 567197, 567177, 1504136, 567196, 567195, 567180, 567181, 1504137, 567188, 1504146, 567128, 1504096, 567131, 567159, 1504120, 1504111, 567130, 1504097, 1504098, 1504089, 1504090, 1504095, 567127, 567140, 567133, 1504101, 567137, 567138, 567114, 567115, 567113, 567112, 567103, 567104, 567101, 567102, 1504076, 567100, 567099, 1504075, 567098, 1504074, 1503954, 566951, 566716, 1503768, 566715, 1503767, 1503766, 566714, 566713, 566712, 1503765, 1503928, 1503929, 566920, 1503927, 566724, 1503774, 566725, 1503777, 566719, 566720, 1503771, 566718, 1503770, 

In [17]:
t1 = time.time()
print(len(nx.dijkstra_path(G, 1, 1805456, 'time')))
print(time.time() - t1)

531
3.1777596473693848


In [6]:
itinerary = shortest_ordered_route(G, 1, [5,8,25,1805456], '')

In [75]:
itinerary

([1,
  1803,
  1802,
  1050022,
  2208,
  2207,
  1050873,
  2866,
  1050871,
  1050346,
  2209,
  2210,
  1050351,
  1050354,
  1050355,
  2231,
  2235,
  2234,
  1050367,
  2230,
  2229,
  2237,
  1050369,
  2238,
  1050368,
  6,
  5,
  1048581,
  8,
  1050376,
  2246,
  1050304,
  1050305,
  2647,
  2157,
  1050306,
  1050308,
  2159,
  34,
  1048603,
  1048598,
  28,
  1050699,
  1050700,
  1048601,
  31,
  1050698,
  1048627,
  64,
  2655,
  2656,
  2657,
  1048626,
  179,
  180,
  35,
  1048604,
  1048606,
  2662,
  1050717,
  2661,
  40,
  1048609,
  1050708,
  43,
  1048612,
  2384,
  1048594,
  23,
  1048594,
  2384,
  1048612,
  43,
  1050708,
  1048609,
  40,
  2661,
  1050717,
  2662,
  1048606,
  1048604,
  35,
  180,
  179,
  1048626,
  2657,
  2656,
  2655,
  64,
  1048627,
  1050698,
  31,
  1048601,
  1050700,
  1050699,
  28,
  1048598,
  1048603,
  34,
  1048603,
  1048598,
  52,
  1050719,
  51,
  1048617,
  2472,
  1048614,
  47,
  46,
  69,
  1048632,
  1048635,
 

In [3]:
G.node[1]['pos'][::-1]

(34.13355, -114.315309)

In [58]:
def viz_map(route, steps):
    m = folium.Map(location=(G.node[1]['pos'][::-1]), zoom_start=13,tiles='openstreetmap')
    
    #add lines
    folium.PolyLine([G.node[elem]['pos'][::-1] for elem in steps], color="red", weight=2.5, opacity=1).add_to(m)
    
    for loc in steps:
        if loc in route:
            folium.CircleMarker(location=G.node[loc]['pos'][::-1], radius=10, line_color='#3186cc',
                    fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)
        else:
            folium.CircleMarker(location=G.node[loc]['pos'][::-1], radius=1, line_color='#3186cc',
                    fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)
    display(m)

In [8]:
viz_map([1,5,23,34,1805456], itinerary[0])

# Framework tests

In [22]:
def bi_dijkstra(graph, start, dest, mode):
    m = folium.Map(location=(G.node[1]['pos'][::-1]), zoom_start=13,tiles='openstreetmap')
    
    # shortest paths is a dict of nodes
    # whose value is a tuple of (previous node, weight)
    # initialize it with the initial node and set it with wight 0
    shortest_paths_start = {start: (None, 0)}
    current_node_start = start
    visited_start = set()
    
    shortest_paths_dest = {dest: (None, 0)}
    current_node_dest = dest
    visited_dest = set()
    
    # create a heap and store the nodes
    # ordered by currend wight
    # heap = []
    heap_start = Fibonacci_heap()
    
    heap_dest = Fibonacci_heap()
    
    folium.CircleMarker(location=G.node[current_node_start]['pos'][::-1], radius=10, line_color='#3186cc',
                    fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)
    folium.CircleMarker(location=G.node[current_node_dest]['pos'][::-1], radius=10, line_color='#3186cc',
                    fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)
    
    
    try:
        while True:
            
            # Add current node to the set of visited nodes
            visited_start.add(current_node_start)
            visited_dest.add(current_node_dest)
            #folium.CircleMarker(location=G.node[current_node_start]['pos'][::-1], radius=1, line_color='#3186cc',
             #       fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)
            folium.CircleMarker(location=G.node[current_node_dest]['pos'][::-1], radius=1, line_color='#3186cc',
                    fill_color='#000000',fill_opacity=0.7, fill=True).add_to(m)

            # adjacency list, take all edges from the current node
            destinations_start = [elem[1] for elem in graph.edges(current_node_start)]
            destinations_dest = [elem[1] for elem in graph.edges(current_node_dest)]
            # take the total weight
            weight_to_current_node_start = shortest_paths_start[current_node_start][1]
            weight_to_current_node_dest = shortest_paths_dest[current_node_dest][1]

            # visit all nodes connected to the current node
            for next_node in destinations_start:
                # test for bidirectional
                if next_node in visited_dest:
                    current_node_dest = next_node
                    raise StopIteration

                # calculate the weight of the current edge
                # weight of the edge + weight of edges previously visited in the path
                weight = get_weight(graph, current_node_start, next_node, mode) + weight_to_current_node_start

                # add nodes to the heap
                if next_node not in visited_start and next_node not in heap_start.nodes:
                    #heappush(heap, (weight, next_node))
                    heap_start.enqueue(next_node, weight)

                # add new node in shortest path
                # or update it if current path is shorter of previous path
                if next_node not in shortest_paths_start:
                    shortest_paths_start[next_node] = (current_node_start, weight)
                else:
                    current_shortest_weight = shortest_paths_start[next_node][1]
                    if current_shortest_weight > weight:
                        shortest_paths_start[next_node] = (current_node_start, weight)

            # visit all nodes connected to the current node
            for next_node in destinations_dest:
                # test for bidirectional
                if next_node in visited_start:
                    current_node_start = next_node
                    raise StopIteration

                # calculate the weight of the current edge
                # weight of the edge + weight of edges previously visited in the path
                weight = get_weight(graph, current_node_dest, next_node, mode) + weight_to_current_node_dest

                # add nodes to the heap
                if next_node not in visited_dest and next_node not in heap_dest.nodes:
                    #heappush(heap, (weight, next_node))
                    heap_dest.enqueue(next_node, weight)

                # add new node in shortest path
                # or update it if current path is shorter of previous path
                if next_node not in shortest_paths_dest:
                    shortest_paths_dest[next_node] = (current_node_dest, weight)
                else:
                    current_shortest_weight = shortest_paths_dest[next_node][1]
                    if current_shortest_weight > weight:
                        shortest_paths_dest[next_node] = (current_node_dest, weight)
        
            # if heap is empty we cannot continue
            # and we cannot reach the destination
            #if len(heap) == 0:
             #   return "Not Possible"

            if not heap_start.__bool__():
                return "Not Possible"
            if not heap_dest.__bool__():
                return "Not Possible"

            # update current_node
            # next node is the destination with the lowest weight
            #current_node = heappop(heap)[1]
            current_node_start = heap_start.dequeue_min().m_elem
            current_node_dest = heap_dest.dequeue_min().m_elem
    
    except StopIteration:
        pass
    
    supp_weight = get_weight(graph, current_node_start, current_node_dest, mode)
    start_weight = shortest_paths_start[current_node_start][1]
    dest_weight = shortest_paths_dest[current_node_dest][1]
    # Work back through destinations in shortest path
    # create path and reverse it
    path = []
    while current_node_start is not None:
        path.append(current_node_start)
        # take previous node from the dict
        next_node = shortest_paths_start[current_node_start][0]
        current_node_start = next_node
    # Reverse path
    path = path[::-1]
    
    print(len(path))
    
    while current_node_dest is not None:
        path.append(current_node_dest)
        # take previous node from the dict
        next_node = shortest_paths_dest[current_node_dest][0]
        current_node_dest = next_node
    
    display(m)
    
    return (path, supp_weight + start_weight + dest_weight)